In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=2, stride=2, padding=0),  
            nn.ELU(),
            nn.Conv2d(32, 32, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(32, 64, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(64, 128, kernel_size=2, stride=2, padding=0),
            nn.ELU(), 
            nn.Conv2d(128, 256, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Conv2d(256, 512, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
from torch.nn.functional import one_hot

class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        visual_features_dim = 512
        target_features_dim = 9 * 11 * 11 
        self.visual_encoder = VisualEncoder()
        self.visual_encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AngelaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.target_encoder = nn.Sequential(
            nn.Conv3d(7, 1, kernel_size=1, stride=1, padding=0),
            nn.ELU(),
        )
        policy_hidden_dim = 256 
        self.policy_network = nn.Sequential(
            nn.Linear(visual_features_dim + target_features_dim, 1024),
            nn.ELU(),
            nn.Linear(1024, 512),
            nn.ELU(),
            nn.Linear(512, policy_hidden_dim),
            nn.ELU(),
            nn.Linear(policy_hidden_dim, policy_hidden_dim),
            nn.ELU(),
            #nn.Linear(policy_hidden_dim, policy_hidden_dim),
            #nn.ELU(),
        )
        self.action_head = nn.Linear(policy_hidden_dim, action_space.n)
        self.value_head = nn.Linear(policy_hidden_dim, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.visual_encoder.cuda()
            self.target_encoder.cuda()
            self.policy_network.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs']
        pov = obs['pov'].permute(0, 3, 1, 2).float() / 255.0
        target = one_hot(obs['target_grid'].long(), num_classes=7).permute(0, 4, 1, 2, 3).float()
        if self.use_cuda:
            pov.cuda()
            target.cuda()
            
        with torch.no_grad():
            visual_features = self.visual_encoder(pov)
            
        target_features = self.target_encoder(target)
        target_features = target_features.reshape(target_features.shape[0], -1)
        features = torch.cat([visual_features, target_features], dim=1)
        features = self.policy_network(features)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
class VisualObservationWrapper(ObsWrapper):
    def __init__(self, env, include_target=False):
        super().__init__(env)
        self.observation_space = {   
            'pov': gym.spaces.Box(low=0, high=255, shape=(64, 64, 3)),
            'inventory': gym.spaces.Box(low=0.0, high=20.0, shape=(6,)),
            'compass': gym.spaces.Box(low=-180.0, high=180.0, shape=(1,))
        }
        if include_target:
            self.observation_space['target_grid'] = \
                gym.spaces.Box(low=0, high=6, shape=(9, 11, 11))
        self.observation_space = gym.spaces.Dict(self.observation_space)

    def observation(self, obs, reward=None, done=None, info=None):
        if info is not None:
            if 'target_grid' in info:
                target_grid = info['target_grid']
                del info['target_grid']
            else:
                logger.error(f'info: {info}')
                if hasattr(self.unwrapped, 'should_reset'):
                    self.unwrapped.should_reset(True)
                target_grid = self.env.unwrapped.tasks.current.target_grid
        else:
            target_grid = self.env.unwrapped.tasks.current.target_grid
        return {
            'pov': obs['pov'].astype(np.float32),
            'inventory': obs['inventory'],
            'compass': np.array([obs['compass']['angle'].item()]),
            'target_grid': target_grid
        }

In [6]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

class RewardWrapper(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
    
    def reward(self, rew):
        if rew == 0:
            rew = -0.01
        return rew
    
def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C3', 'C17', 'C32']))
    #env = PovOnlyWrapper(env)
    env = VisualObservationWrapper(env, include_target=True)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    env = RewardWrapper(env)
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [ ]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             #"gamma": 0.99,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name": "PPO MultiTask (C3, C17, C32) pretrained (AngelaCNN) (3 noops after placement) r: -0.01"
                  }
              }

        },
        loggers=[WandbLogger],
        local_dir="/IGLU-Minecraft/checkpoints/",
        keep_checkpoints_num=50,
        checkpoint_freq=5,
        checkpoint_at_end=True)

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)


2021-11-05 12:31:42,213	INFO wandb.py:170 -- Already logged into W&B.
2021-11-05 12:31:42,226	ERROR syncer.py:72 -- Log sync requires rsync to be installed.
wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id 0f10e_00000 but id 549f0_00000 is set.
wandb: wandb version 0.12.6 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=307252) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=307252)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=307252) 2021-11-05 12:31:45,655	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=307252) 2021-11-05 12:31:45,655	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=307262) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=307262)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=307252) 2021-11-05 12:31:51,375	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=307262) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=307262)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=307262) /root/miniconda/envs/py37/lib/py

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-11-05_12-32-52
  done: false
  episode_len_mean: 393.0
  episode_media: {}
  episode_reward_max: -7.769999999999953
  episode_reward_mean: -14.065000000000035
  episode_reward_min: -20.360000000000117
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.882830344306098
          entropy_coeff: 0.009999999999999998
          kl: 0.00782593100867451
          policy_loss: 0.11407342735264037
          total_loss: 0.5807270208166705
          vf_explained_var: 0.2950565218925476
          vf_loss: 0.4939167136947314
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_s

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-11-05_12-33-12
  done: false
  episode_len_mean: 402.25
  episode_media: {}
  episode_reward_max: -4.109999999999957
  episode_reward_mean: -9.089999999999996
  episode_reward_min: -20.360000000000117
  episodes_this_iter: 2
  episodes_total: 4
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8729226801130507
          entropy_coeff: 0.009999999999999998
          kl: 0.008935499472480816
          policy_loss: -0.06010568820767932
          total_loss: -0.07399718142631981
          vf_explained_var: 0.4425891935825348
          vf_loss: 0.013050633063539863
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  itera

...

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1321000
  custom_metrics: {}
  date: 2021-11-05_21-56-57
  done: false
  episode_len_mean: 300.3
  episode_media: {}
  episode_reward_max: -2.3699999999999934
  episode_reward_mean: -3.00299999999998
  episode_reward_min: -4.0299999999999585
  episodes_this_iter: 3
  episodes_total: 4896
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.18171470346189586
          cur_lr: 5.000000000000001e-05
          entropy: 1.0831775354014503
          entropy_coeff: 0.009999999999999998
          kl: 0.010121352283082826
          policy_loss: 0.018981050699949265
          total_loss: 0.018476125680738024
          vf_explained_var: 0.5263505578041077
          vf_loss: 0.008487651277230017
    num_agent_steps_sampled: 1321000
    num_agent_steps_trained: 1321000
    num_steps_sampled: 1321000
    num_steps_trained

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1322000
  custom_metrics: {}
  date: 2021-11-05_21-57-19
  done: false
  episode_len_mean: 300.19
  episode_media: {}
  episode_reward_max: -2.3699999999999934
  episode_reward_mean: -3.00189999999998
  episode_reward_min: -4.0299999999999585
  episodes_this_iter: 3
  episodes_total: 4899
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.18171470346189586
          cur_lr: 5.000000000000001e-05
          entropy: 0.993696555826399
          entropy_coeff: 0.009999999999999998
          kl: 0.006093254651521147
          policy_loss: -0.07985732166303529
          total_loss: -0.07876977564560042
          vf_explained_var: 0.5749735236167908
          vf_loss: 0.009917275617933936
    num_agent_steps_sampled: 1322000
    num_agent_steps_trained: 1322000
    num_steps_sampled: 1322000
    num_steps_trained

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1323000
  custom_metrics: {}
  date: 2021-11-05_21-57-42
  done: false
  episode_len_mean: 297.76
  episode_media: {}
  episode_reward_max: -2.3699999999999934
  episode_reward_mean: -2.97759999999998
  episode_reward_min: -3.9999999999999587
  episodes_this_iter: 4
  episodes_total: 4903
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.18171470346189586
          cur_lr: 5.000000000000001e-05
          entropy: 1.0091561641958025
          entropy_coeff: 0.009999999999999998
          kl: 0.007129837429685418
          policy_loss: 0.030874348017904493
          total_loss: 0.02986754741933611
          vf_explained_var: 0.7322816848754883
          vf_loss: 0.007789160957973864
    num_agent_steps_sampled: 1323000
    num_agent_steps_trained: 1323000
    num_steps_sampled: 1323000
    num_steps_trained

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1324000
  custom_metrics: {}
  date: 2021-11-05_21-58-05
  done: false
  episode_len_mean: 296.99
  episode_media: {}
  episode_reward_max: -2.3699999999999934
  episode_reward_mean: -2.96989999999998
  episode_reward_min: -3.9999999999999587
  episodes_this_iter: 4
  episodes_total: 4907
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.18171470346189586
          cur_lr: 5.000000000000001e-05
          entropy: 0.8667469693554772
          entropy_coeff: 0.009999999999999998
          kl: 0.008209378178811575
          policy_loss: -0.033513271684447926
          total_loss: -0.03125533424317837
          vf_explained_var: 0.5963281989097595
          vf_loss: 0.009433642314333055
    num_agent_steps_sampled: 1324000
    num_agent_steps_trained: 1324000
    num_steps_sampled: 1324000
    num_steps_train

Result for PPO_my_env_549f0_00000:
  agent_timesteps_total: 1325000
  custom_metrics: {}
  date: 2021-11-05_21-58-27
  done: false
  episode_len_mean: 296.87
  episode_media: {}
  episode_reward_max: -2.3699999999999934
  episode_reward_mean: -2.9686999999999806
  episode_reward_min: -3.9999999999999587
  episodes_this_iter: 3
  episodes_total: 4910
  experiment_id: 84379fbd193c493d824c19bcb2dbb009
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.18171470346189586
          cur_lr: 5.000000000000001e-05
          entropy: 1.0396046969625685
          entropy_coeff: 0.009999999999999998
          kl: 0.00845061312432074
          policy_loss: 0.03101274644335111
          total_loss: 0.03195282303624683
          vf_explained_var: 0.3669999837875366
          vf_loss: 0.009800523648866348
    num_agent_steps_sampled: 1325000
    num_agent_steps_trained: 1325000
    num_steps_sampled: 1325000
    num_steps_trained